# GET KLUE DATASET

In [1]:
!pip install datasets

     |████████████████████████████████| 266kB 6.6MB/s 
     |████████████████████████████████| 245kB 31.2MB/s 
     |████████████████████████████████| 122kB 42.3MB/s 


In [2]:
import datasets
import pandas as pd

In [3]:
klue_dataset = datasets.load_dataset("klue", "mrc").remove_columns(['answers', 'guid', 'is_impossible', 'question', 'question_type', 'source', 'title'])
train_dataset = pd.DataFrame(klue_dataset['train'])
val_dataset = pd.DataFrame(klue_dataset['validation'])

Dataset klue downloaded and prepared to /root/.cache/huggingface/datasets/klue/mrc/1.0.0/55ff8f92b7a4b9842be6514ce0b4b5295b46d5e493f8bb5760da4be717018f90. Subsequent calls will reuse this data.


In [4]:
train_dataset.head(5)

context news_category
0  올여름 장마가 17일 제주도에서 시작됐다. 서울 등 중부지방은 예년보다 사나흘 정도...            종합
1  부산시와 (재)부산정보산업진흥원(원장 이인숙)이 ‘2020~2021년 지역SW서비스...            경제
2  부산시와 (재)부산정보산업진흥원(원장 이인숙)이 ‘2020~2021년 지역SW서비스...            경제
3  미국 세인트루이스에서 태어났고, 프린스턴 대학교에서 학사 학위를 마치고 1939년에...          None
4  시범 경기에서는 16이닝을 던져 15실점을 기록하는 등 성적이 좋지 않았지만 본인으...          None

# TRAIN & VAL DATA
- context 중복 제거
- use only 5 category
    - 사회, 국제, 부동산, 경제, 산업섹션

In [5]:
train_dataset = train_dataset.drop_duplicates(subset=['context'])
val_dataset = val_dataset.drop_duplicates(subset=['context'])

In [6]:
train_dataset.groupby('news_category').count().sort_values(by='context', ascending=False)

context
news_category         
종합                1838
사회                 717
국제                 577
부동산                549
경제                 537
산업섹션               532
문화/TV              434
생활경제               370
기획                 319
금융                 301
기업&CEO             291
미디어                255
생활                 249
게임                 239
산업                 235
자동차                216
테크                 209
IT모바일              207
책마을                206
전국                 137
중기                 135
IT 과학              107
중기 의료               89
기업&IT               77
중기과학                71
경제금융                69
JOB                 68
교육산업                55
과학                  49
로&비즈                46
커버스토리               35
생생헬스                20
                     3

In [7]:
using_categories = set(train_dataset.groupby('news_category').count().sort_values(by='context', ascending=False).iloc[1:6].index)
using_categories

{'경제', '국제', '부동산', '사회', '산업섹션'}

In [8]:
train_dataset = train_dataset[train_dataset['news_category'].isin(using_categories)]
val_dataset = val_dataset[val_dataset['news_category'].isin(using_categories)]

In [9]:
train_dataset.groupby('news_category').count().sort_values(by='context', ascending=False)

context
news_category         
사회                 717
국제                 577
부동산                549
경제                 537
산업섹션               532

# PRE-PROCESSING

In [10]:
import re

In [35]:
processed_train_dataset = [re.sub('[^가-힣a-zA-Z0-9\s]', '', x) for x in train_dataset['context']]
processed_val_dataset = [re.sub('[^가-힣a-zA-Z0-9\s]', '', x) for x in val_dataset['context']]

In [68]:
train_dataset['context'].iloc[0]

'부산시와 (재)부산정보산업진흥원(원장 이인숙)이 ‘2020~2021년 지역SW서비스사업화 지원사업’ 공모사업에 4개 과제가 선정되어 본격적인 사업 착수에 나선다. 과학기술정보통신부가 주관하는 ‘지역SW서비스사업화 지원사업’은 강소SW기업 및 초기 스타트업의 SW서비스 사업화 지원과 신시장 진출 지원을 통해 기업 경쟁력 강화와 지역경제 활성화를 도모하는 사업이다. 올해부터 2개년으로 진행되며, 국비와 시비, 민자 등 2년간 약 37억원의 예산이 투입된다. 앞서 진흥원은 부산의 미래 먹거리산업인 스마트해양, 지능형기계, 지능정보서비스 분야로 사전 수요조사를 진행했고, 평가를 통해 선정된 5개 과제를 공모사업에 신청했다. 그 결과 부산의 4개 과제가 최종 선정되는 쾌거를 거뒀다. 당 사업은 전국 진흥기관을 대상으로 공모를 시작해, 총 17개 지역에서 42개 과제가 선정되었으며, 4개 과제가 선정된 곳은 부산과 강원지역 뿐이다. 금번 선정된 과제들은 ‘인공지능융합센서와 서보 이송 로봇을 이용한 전단보강재의 자동용접시스템 개발’ 등 총 4개 과제다. 부산시가 지원하고, 부산정보산업진흥원과 지역기업, 대학, 연구소 등이 컨소시엄을 구성하여 기술개발 및 사업화 지원을 추진한다. 2개의 Track으로 구분되는 이번사업은 Track 1(SW중소기업)에서 ㈜에이아이플랫폼, 엔컴(주), Track 2(스타트업)에서는 ㈜토즈, 삼보테크놀로지를 지원한다. ○ ‘Track 1‘의 (주)에이아이플랫폼이 주관기업으로 진행하는 <인공지능 기반 망막 내 아밀로이드 플라크 영상 분석을 통한 치매조기진단 플랫폼 상용화>는 치매 확진의 원인이 되는 중요 단백질(아밀로이드 플라크)을 자체개발 관측장비로 진단한다. 이를 통해 치매를 조기 발견하여, 각종 경제적 비용과 치료 및 예방 등 사회적 문제를 해 결하고 시민들이 쉽게 접근 가능한 실효성 있는 치매관리체계 개발을 목표로 한다. ○ 엔컴(주)이 주관기업으로 참여하는 <AI영상분석 기반 가공철근 생산성 향상 시스템 기술개발 및 사업화>는 산업안전,

In [69]:
processed_train_dataset[0]

'부산시와 재부산정보산업진흥원원장 이인숙이 20202021년 지역SW서비스사업화 지원사업 공모사업에 4개 과제가 선정되어 본격적인 사업 착수에 나선다 과학기술정보통신부가 주관하는 지역SW서비스사업화 지원사업은 강소SW기업 및 초기 스타트업의 SW서비스 사업화 지원과 신시장 진출 지원을 통해 기업 경쟁력 강화와 지역경제 활성화를 도모하는 사업이다 올해부터 2개년으로 진행되며 국비와 시비 민자 등 2년간 약 37억원의 예산이 투입된다 앞서 진흥원은 부산의 미래 먹거리산업인 스마트해양 지능형기계 지능정보서비스 분야로 사전 수요조사를 진행했고 평가를 통해 선정된 5개 과제를 공모사업에 신청했다 그 결과 부산의 4개 과제가 최종 선정되는 쾌거를 거뒀다 당 사업은 전국 진흥기관을 대상으로 공모를 시작해 총 17개 지역에서 42개 과제가 선정되었으며 4개 과제가 선정된 곳은 부산과 강원지역 뿐이다 금번 선정된 과제들은 인공지능융합센서와 서보 이송 로봇을 이용한 전단보강재의 자동용접시스템 개발 등 총 4개 과제다 부산시가 지원하고 부산정보산업진흥원과 지역기업 대학 연구소 등이 컨소시엄을 구성하여 기술개발 및 사업화 지원을 추진한다 2개의 Track으로 구분되는 이번사업은 Track 1SW중소기업에서 에이아이플랫폼 엔컴주 Track 2스타트업에서는 토즈 삼보테크놀로지를 지원한다  Track 1의 주에이아이플랫폼이 주관기업으로 진행하는 인공지능 기반 망막 내 아밀로이드 플라크 영상 분석을 통한 치매조기진단 플랫폼 상용화는 치매 확진의 원인이 되는 중요 단백질아밀로이드 플라크을 자체개발 관측장비로 진단한다 이를 통해 치매를 조기 발견하여 각종 경제적 비용과 치료 및 예방 등 사회적 문제를 해 결하고 시민들이 쉽게 접근 가능한 실효성 있는 치매관리체계 개발을 목표로 한다  엔컴주이 주관기업으로 참여하는 AI영상분석 기반 가공철근 생산성 향상 시스템 기술개발 및 사업화는 산업안전 환경규제 생산체계의 변화로 침체된 부산 핵심 산업인 철강업 활성화에 나선다 실시간으로 절곡되어 나오는 가

# TfidfVectorizer

## without tokenizer

In [38]:
from sklearn.feature_extraction.text import TfidfVectorizer

In [45]:
vectorizer = TfidfVectorizer()
train_x_data = vectorizer.fit_transform(processed_train_dataset)
train_y_data = train_dataset['news_category']

print(vectorizer.get_feature_names())
print(train_x_data.shape, train_y_data.shape)

['0001초', '001', '0011로', '0016', '001달러까지', '002', '002003에', '0025다', '0025인', '002h로', '002과', '002포인트', '003', '003사진이', '003포인트', '004', '0043에', '004에', '004포인트', '005', '005009로', '005h', '005달러에', '005로', '005의', '005포인트', '006', '006490가', '006h', '006와', '006포인트', '006포인트와', '007', '007기가', '007에', '007와', '008까지', '008포인트', '009', '0091제곱피트당', '0094포인트', '009로', '009에', '009포인트', '00로', '00명을', '00명의', '01', '01020694474', '01022211402서울', '01022905981', '01022905981충남', '01023685949경기', '01024433922', '01025332951경북', '01025332951충남', '01027915050제주', '01029115800', '01031189678경기', '01031690776경기', '01031690776서울', '01031882700서울', '01033219326서울', '01033789600', '01036515595', '01036515595서울', '01037378401인천', '01042152002', '01043960027경기', '01043960027충남', '01046678856대전', '01052571020', '01053059797', '01056232600서울', '01057047300', '01085611477충남', '01088559483서울', '01089356236', '01089905049', '01089905049충남', '01090002969', '01090002969경기', '01094691889서울', '0109588

In [41]:
val_x_data = vectorizer.transform(processed_val_dataset)
val_y_data = val_dataset['news_category']

## KoNLPy tokenizer

In [42]:
!pip install konlpy

     |████████████████████████████████| 19.4MB 1.5MB/s 
     |████████████████████████████████| 92kB 8.5MB/s 
     |████████████████████████████████| 450kB 34.5MB/s 
  Found existing installation: beautifulsoup4 4.6.3
    Uninstalling beautifulsoup4-4.6.3:
      Successfully uninstalled beautifulsoup4-4.6.3


In [43]:
from sklearn.feature_extraction.text import TfidfVectorizer
from konlpy.tag import Komoran
from tqdm import tqdm_notebook

In [46]:
tokenizer = Komoran()
vectorizer = TfidfVectorizer(tokenizer=lambda x: tokenizer.morphs(x))

In [47]:
train_x_data = vectorizer.fit_transform(processed_train_dataset)
train_y_data = train_dataset['news_category']

print(vectorizer.get_feature_names())
print(train_x_data.shape, train_y_data.shape)

['0', '00', '0001', '001', '0011', '0016', '002', '002003', '0025', '003', '004', '0043', '005', '005009', '006', '006490', '007', '007980', '008', '009', '0091', '0094', '01', '010', '01020694474', '01022211402', '01022905981', '01023685949', '01024433922', '01025332951', '01027915050', '01029115800', '01031189678', '01031690776', '01031882700', '01033219326', '01033789600', '01036515595', '01037378401', '01042152002', '01043960027', '01046678856', '01052571020', '01053059797', '01056232600', '01057047300', '01085611477', '01088559483', '01089356236', '01089905049', '01090002969', '01094691889', '01095888959', '011', '01197076010', '01197587389', '012', '013', '0139', '014', '015', '0152', '0158', '016', '017', '0179', '018', '019', '0197', '02', '020', '0203', '0205', '021', '022', '0221331596', '0222806801', '0226710621', '023', '023086900', '0232709219', '0234449877', '0234468100', '023604054', '02377165046', '024', '025', '025078335', '025113215', '025113390', '025113398', '025119

In [48]:
val_x_data = vectorizer.transform(processed_val_dataset)
val_y_data = val_dataset['news_category']

# CLASSIFICATION

## RANDOM FOREST

In [49]:
from sklearn.ensemble import RandomForestClassifier

In [50]:
random_forest = RandomForestClassifier()
random_forest.fit(train_x_data, train_y_data)

RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criterion='gini', max_depth=None, max_features='auto',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=None,
                       verbose=0, warm_start=False)

In [51]:
random_forest_preds = random_forest.predict(val_x_data)

In [52]:
for ctxt, true, pred in zip(val_dataset['context'], val_y_data, random_forest_preds):
    print(f'context: {ctxt}')
    print(f'true: {true}\tpreds: {pred}\n')

context: 프랑스 남부 알프스에 떨어져 150명의 사망자를 낸 저먼윙스 여객기는 부조종사가 의도적으로 추락시킨 것으로 보인다고 프랑스 검찰이 26일 발표했다.AFP통신 등에 따르면 사건을 조사 중인 프랑스 검찰의 브리스 로뱅 검사는 이날 기자회견을 열어 “조종실 음성녹음장치를 확인한 결과 조종사가 조종실 밖으로 나간 사이 부조종사가 의도적으로 여객기를 파괴하려 한 것 같다”고 밝혔다.로뱅 검사는 “부조종사가 의도적으로 여객기 하강버튼을 눌렀고, 여객기의 하강속도가 빨라졌다”며 “사고 직전 조종석 밖에 있던 조종사가 문을 여러 차례 두드리고 소리를 질렀지만, 부조종사는 문을 열지 않았다”고 설명했다. 그는 “마지막 순간까지 부조종사의 호흡은 정상이었으며 조종실에서는 침묵이 흘렀다”고 덧붙였다.부조종사는 28세인 독일 국적의 안드레아스 루비츠로, 1년6개월 전 조종간을 잡기 시작했으며 비행시간 경력은 630시간인 것으로 파악됐다. 로뱅 검사는 “부조종사의 테러 연관성은 확인되지 않았다”며 “테러 공격이라고 의심할 만한 이유는 없다”고 말했다. 저먼윙스 여객기는 지난 24일 스페인 바르셀로나에서 독일 뒤셀도르프로 향하던 중 마지막 교신이 이뤄지고 나서 약 8분간 3만2000피트(약 9754ｍ)를 급강하해 알프스 산을 들이받았다. 로뱅 검사는 “여객기가 추락할 때 프랑스 관제탑이 ‘메이데이’라는 조난신호를 받지 못했다”고 말했다. 이 사고로 승객 144명과 승무원 6명 등 탑승자 150명이 모두 사망했다.
true: 국제	preds: 국제

context: 가장 일하고 싶은 회사로 미국 컨설팅 업체인 베인&컴퍼니가 선정됐다. 트위터와 링크트인, 페이스북 등 정보기술(IT) 기업에 대한 선호도 높게 나타났다. 미국 경제전문지 포브스는 “채용 사이트인 글라스도어가 미국에서 일하는 50만명의 직장인을 대상으로 설문조사를 벌여 ‘2014년 일하고 싶은 50대 회사’를 선정했다”고 11일(현지시간) 보도했다. 베인&컴퍼니는 2012년에 이어 두 번째로 1위에 올랐다. 하

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [53]:
from sklearn.metrics import f1_score, accuracy_score, confusion_matrix

In [54]:
macro_f1 = f1_score(val_y_data, random_forest_preds, average='macro')
micro_f1 = f1_score(val_y_data, random_forest_preds, average='micro')
acc = accuracy_score(val_y_data, random_forest_preds)

In [55]:
print(f'macro_f1: {macro_f1}')
print(f'micro_f1: {micro_f1}')
print(f'accuracy: {acc}')

macro_f1: 0.8966210363509614
micro_f1: 0.8980944490472246
accuracy: 0.8980944490472246


In [56]:
random_forest.classes_

array(['경제', '국제', '부동산', '사회', '산업섹션'], dtype=object)

In [57]:
confusion_matrix(val_y_data, random_forest_preds)

array([[154,   9,   4,  49,   5],
       [  0, 233,   0,   4,   4],
       [  1,   0, 221,   9,   3],
       [  8,   1,   5, 264,   3],
       [  5,   6,   0,   7, 212]])

## MLP CLASSIFIER (DNN)

In [58]:
from sklearn.neural_network import MLPClassifier

In [59]:
dnn = MLPClassifier(batch_size=64, verbose=True, max_iter=10).fit(train_x_data, train_y_data)
dnn_preds = dnn.predict(val_x_data)

Iteration 1, loss = 1.41216935
Iteration 2, loss = 0.81533630
Iteration 3, loss = 0.38773183
Iteration 4, loss = 0.19440299
Iteration 5, loss = 0.10953062
Iteration 6, loss = 0.06881468
Iteration 7, loss = 0.04705751
Iteration 8, loss = 0.03435262
Iteration 9, loss = 0.02625752
Iteration 10, loss = 0.02090720


/usr/local/lib/python3.7/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:571: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (10) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)


In [60]:
for ctxt, true, pred in zip(val_dataset['context'], val_y_data, dnn_preds):
    print(f'context: {ctxt}')
    print(f'true: {true}\tpreds: {pred}\n')

context: 프랑스 남부 알프스에 떨어져 150명의 사망자를 낸 저먼윙스 여객기는 부조종사가 의도적으로 추락시킨 것으로 보인다고 프랑스 검찰이 26일 발표했다.AFP통신 등에 따르면 사건을 조사 중인 프랑스 검찰의 브리스 로뱅 검사는 이날 기자회견을 열어 “조종실 음성녹음장치를 확인한 결과 조종사가 조종실 밖으로 나간 사이 부조종사가 의도적으로 여객기를 파괴하려 한 것 같다”고 밝혔다.로뱅 검사는 “부조종사가 의도적으로 여객기 하강버튼을 눌렀고, 여객기의 하강속도가 빨라졌다”며 “사고 직전 조종석 밖에 있던 조종사가 문을 여러 차례 두드리고 소리를 질렀지만, 부조종사는 문을 열지 않았다”고 설명했다. 그는 “마지막 순간까지 부조종사의 호흡은 정상이었으며 조종실에서는 침묵이 흘렀다”고 덧붙였다.부조종사는 28세인 독일 국적의 안드레아스 루비츠로, 1년6개월 전 조종간을 잡기 시작했으며 비행시간 경력은 630시간인 것으로 파악됐다. 로뱅 검사는 “부조종사의 테러 연관성은 확인되지 않았다”며 “테러 공격이라고 의심할 만한 이유는 없다”고 말했다. 저먼윙스 여객기는 지난 24일 스페인 바르셀로나에서 독일 뒤셀도르프로 향하던 중 마지막 교신이 이뤄지고 나서 약 8분간 3만2000피트(약 9754ｍ)를 급강하해 알프스 산을 들이받았다. 로뱅 검사는 “여객기가 추락할 때 프랑스 관제탑이 ‘메이데이’라는 조난신호를 받지 못했다”고 말했다. 이 사고로 승객 144명과 승무원 6명 등 탑승자 150명이 모두 사망했다.
true: 국제	preds: 국제

context: 가장 일하고 싶은 회사로 미국 컨설팅 업체인 베인&컴퍼니가 선정됐다. 트위터와 링크트인, 페이스북 등 정보기술(IT) 기업에 대한 선호도 높게 나타났다. 미국 경제전문지 포브스는 “채용 사이트인 글라스도어가 미국에서 일하는 50만명의 직장인을 대상으로 설문조사를 벌여 ‘2014년 일하고 싶은 50대 회사’를 선정했다”고 11일(현지시간) 보도했다. 베인&컴퍼니는 2012년에 이어 두 번째로 1위에 올랐다. 하

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [61]:
macro_f1 = f1_score(val_y_data, dnn_preds, average='macro')
micro_f1 = f1_score(val_y_data, dnn_preds, average='micro')
acc = accuracy_score(val_y_data, dnn_preds)

print(f'macro_f1: {macro_f1}')
print(f'micro_f1: {micro_f1}')
print(f'accuracy: {acc}')

macro_f1: 0.933071615407662
micro_f1: 0.9328914664457332
accuracy: 0.9328914664457332


In [62]:
dnn.classes_

array(['경제', '국제', '부동산', '사회', '산업섹션'], dtype='<U4')

In [63]:
confusion_matrix(val_y_data, dnn_preds)

array([[188,   4,   2,  21,   6],
       [  0, 236,   0,   1,   4],
       [  2,   1, 225,   5,   1],
       [ 15,   2,   5, 257,   2],
       [  4,   1,   0,   5, 220]])